# Circuit Design

The main challenge of circuit design is the contradiction between

- Expressibility
- Trainability


Here are several routes to create circuits

- Hardware efficient ansatz (n-local circuit)

    The general structure of n-local circuit looks like


        ┌──────┐ ░ ┌──────┐                      ░ ┌──────┐
        ┤0     ├─░─┤0     ├──────────────── ... ─░─┤0     ├
        │  Rot │ ░ │      │┌──────┐              ░ │  Rot │
        ┤1     ├─░─┤1     ├┤0     ├──────── ... ─░─┤1     ├
        ├──────┤ ░ │  Ent ││      │┌──────┐      ░ ├──────┤
        ┤0     ├─░─┤2     ├┤1     ├┤0     ├ ... ─░─┤0     ├
        │  Rot │ ░ │      ││  Ent ││      │      ░ │  Rot │
        ┤1     ├─░─┤3     ├┤2     ├┤1     ├ ... ─░─┤1     ├
        ├──────┤ ░ └──────┘│      ││  Ent │      ░ ├──────┤
        ┤0     ├─░─────────┤3     ├┤2     ├ ... ─░─┤0     ├
        │  Rot │ ░         └──────┘│      │      ░ │  Rot │
        ┤1     ├─░─────────────────┤3     ├ ... ─░─┤1     ├
        └──────┘ ░                 └──────┘      ░ └──────┘

                |                                 |
                +---------------------------------+
                    repeated reps times

    Specially, if the Ent gates are two-qubit gates, n-local ansatz becomes 2-local.

    Both n-local and 2-local have been included in qiskit.circuit.library.

    The basic usage is

        ```
        from qiskit.circuit.library import NLocal, TwoLocal

        NLocal(
            num_qubits,
            rotation_blocks,
            entanglement_blocks,
            entanglement                = "full",
            reps                        = 3,
            skip_final_rotation_layer   = False,
            skip_unentangled_qubits     = False,
            insert_barriers             = False,
            initial_state               = None,
            parameter_prefix            = "0",
            name                        = 'NLocal',
            flatten                     = False,
        )
        ```

    There are also several special and widely used ansatz, including:

    - [Efficient SU2 2-local circuit](##Efficient-SU2-2-local-circuit)
    - [Real-amplitudes 2-local circuit](##Real-amplitudes-2-local-circuit)
    - [Pauli 2-design ansatz](##Pauli-Two-Design-ansatz)
    - [Excitation preserving circuit](##Excitation-Preserving-circuit)


- Problem inspired ansatz

    - Unitary cluster coupling (UCC)
    - ADAPT


- Circuit search

    - Quantum noise-adaptive-search
    - Quantum architecture search

In [1]:
# Get hardware backends

from huayi_providers.fake_huayi30 import FakeHuayi30
from qiskit_ionq import IonQProvider
from qiskit.providers.fake_provider import *
from qiskit_aer.noise.noise_model import NoiseModel

# "fakeionq" is de facto a generic backend with all kinds of gates
fakehuayi = FakeHuayi30()
fakeionq = IonQProvider().get_backend("ionq_simulator")
fakemontreal = FakeMontreal()

## Efficient SU2 2-local circuit

The ``EfficientSU2`` constraints the entanglement blocks be ``CX``, the rotation gates can be customized by ``su2_gates``.

In [73]:
from qiskit.circuit.library import EfficientSU2
from qiskit import transpile
from qiskit import QuantumCircuit
from qiskit.circuit.library.standard_gates import RXGate, RYGate, CZGate, CXGate, CYGate

n_qubits = 4
ent_pairs = [[i, i+1] for i in range(0,n_qubits,2)] + \
            [[i-1, i] for i in range(2,n_qubits,2)]
ansatz_effsu2 = EfficientSU2(n_qubits, 
                             su2_gates=['rz'],
                             entanglement=ent_pairs, 
                             insert_barriers=True,
                             reps=1,
                             flatten=True)
# ansatz_effsu2._entanglement_blocks = CYGate

print("Efficient SU2 ansatz")
print(ansatz_effsu2.draw(fold=400, idle_wires=False))

c_montreal = transpile(ansatz_effsu2, backend=fakemontreal, optimization_level=3)
print("Transpileed with Montreal backend, depth = {}".format(c_montreal.depth()))
print(c_montreal.draw(fold=160, idle_wires=False))

c_huayi = transpile(ansatz_effsu2, backend=fakehuayi, optimization_level=3)
print("Transpileed with Huayi backend, depth = {}".format(c_huayi.depth()))
print(c_huayi.draw(fold=400, idle_wires=False))

Efficient SU2 ansatz
     ┌──────────┐ ░            ░ ┌──────────┐
q_0: ┤ Rz(θ[0]) ├─░───■────────░─┤ Rz(θ[4]) ├
     ├──────────┤ ░ ┌─┴─┐      ░ ├──────────┤
q_1: ┤ Rz(θ[1]) ├─░─┤ X ├──■───░─┤ Rz(θ[5]) ├
     ├──────────┤ ░ └───┘┌─┴─┐ ░ ├──────────┤
q_2: ┤ Rz(θ[2]) ├─░───■──┤ X ├─░─┤ Rz(θ[6]) ├
     ├──────────┤ ░ ┌─┴─┐└───┘ ░ ├──────────┤
q_3: ┤ Rz(θ[3]) ├─░─┤ X ├──────░─┤ Rz(θ[7]) ├
     └──────────┘ ░ └───┘      ░ └──────────┘
Transpileed with Montreal backend, depth = 4
          ┌──────────┐ ░ ┌───┐      ░ ┌──────────┐
 q_3 -> 8 ┤ Rz(θ[3]) ├─░─┤ X ├──────░─┤ Rz(θ[7]) ├
          ├──────────┤ ░ └─┬─┘┌───┐ ░ ├──────────┤
q_2 -> 11 ┤ Rz(θ[2]) ├─░───■──┤ X ├─░─┤ Rz(θ[6]) ├
          ├──────────┤ ░      └─┬─┘ ░ ├──────────┤
q_0 -> 13 ┤ Rz(θ[0]) ├─░───■────┼───░─┤ Rz(θ[4]) ├
          ├──────────┤ ░ ┌─┴─┐  │   ░ ├──────────┤
q_1 -> 14 ┤ Rz(θ[1]) ├─░─┤ X ├──■───░─┤ Rz(θ[5]) ├
          └──────────┘ ░ └───┘      ░ └──────────┘
Transpileed with Huayi backend, depth = 10
global phase: π
  

## Real-amplitudes 2-local circuit

``RealAmplitudes`` is a special ``Efficient SU2`` with the rotation gates being ``Ry``.

``RealAmplitudes`` is called so because the prepared quantum states will only have real amplitude.

In [23]:
from qiskit.circuit.library import RealAmplitudes

n_qubits = 4
ansatz_realamp = RealAmplitudes(n_qubits,
                                reps=1,
                                insert_barriers=True,
                                flatten=True
                                )

print("Pauli Two-Design ansatz")
print(ansatz_realamp.draw(fold=160, idle_wires=False))

c_montreal = transpile(ansatz_realamp, backend=fakemontreal, optimization_level=3)
print("Transpileed with Montreal backend, depth = {}".format(c_montreal.depth()))
print(c_montreal.draw(fold=160, idle_wires=False))

c_huayi = transpile(ansatz_realamp, backend=fakehuayi, optimization_level=3)
print("Transpileed with Huayi backend, depth = {}".format(c_huayi.depth()))
print(c_huayi.draw(fold=160, idle_wires=False))

Pauli Two-Design ansatz
     ┌──────────┐ ░                 ░ ┌──────────┐
q_0: ┤ Ry(θ[0]) ├─░─────────────■───░─┤ Ry(θ[4]) ├
     ├──────────┤ ░           ┌─┴─┐ ░ ├──────────┤
q_1: ┤ Ry(θ[1]) ├─░────────■──┤ X ├─░─┤ Ry(θ[5]) ├
     ├──────────┤ ░      ┌─┴─┐└───┘ ░ ├──────────┤
q_2: ┤ Ry(θ[2]) ├─░───■──┤ X ├──────░─┤ Ry(θ[6]) ├
     ├──────────┤ ░ ┌─┴─┐└───┘      ░ ├──────────┤
q_3: ┤ Ry(θ[3]) ├─░─┤ X ├───────────░─┤ Ry(θ[7]) ├
     └──────────┘ ░ └───┘           ░ └──────────┘
Transpileed with Montreal backend, depth = 11
          ┌────┐┌──────────────┐┌────┐┌────────┐ ░ ┌───┐           ░ ┌────┐┌──────────────┐┌────┐┌────────┐
 q_3 -> 8 ┤ √X ├┤ Rz(θ[3] + π) ├┤ √X ├┤ Rz(3π) ├─░─┤ X ├───────────░─┤ √X ├┤ Rz(θ[7] + π) ├┤ √X ├┤ Rz(3π) ├
          ├────┤├──────────────┤├────┤├────────┤ ░ └─┬─┘┌───┐      ░ ├────┤├──────────────┤├────┤├────────┤
q_2 -> 11 ┤ √X ├┤ Rz(θ[2] + π) ├┤ √X ├┤ Rz(3π) ├─░───■──┤ X ├──────░─┤ √X ├┤ Rz(θ[6] + π) ├┤ √X ├┤ Rz(3π) ├
          ├────┤├──────────────┤├────┤├

## Pauli Two-Design ansatz

Pauli 2-design is a little different from 2-local because its rotation layers contain random rotations gates ``RX``, ``RY`` or ``RZ``. The choice depends on ``seed``.

The entenlement blocks are constrained to be ``CZ``.

It says that Pauli 2-design is frequently studied in quantum machine learning literature, such as e.g. the investigating of Barren plateaus in variational algorithms.


In [56]:
from qiskit.circuit.library import PauliTwoDesign

n_qubits = 4
ansatz_pauli2des = PauliTwoDesign(n_qubits, 
                                  reps=1,
                                  seed=120,
                                  insert_barriers=True
                                  )
ansatz_pauli2des._flatten=True

print("Pauli Two-Design ansatz")
print(ansatz_pauli2des.draw(fold=160, idle_wires=False))

c_montreal = transpile(ansatz_pauli2des, backend=fakemontreal, optimization_level=3)
print("Transpileed with Montreal backend, depth = {}".format(c_montreal.depth()))
print(c_montreal.draw(fold=160, idle_wires=False))

c_huayi = transpile(ansatz_pauli2des, backend=fakehuayi, optimization_level=3)
print("Transpileed with Huayi backend, depth = {}".format(c_huayi.depth()))
print(c_huayi.draw(fold=160, idle_wires=False))

Pauli Two-Design ansatz
     ┌─────────┐ ░ ┌──────────┐       ░ ┌──────────┐
q_0: ┤ Ry(π/4) ├─░─┤ Rx(θ[0]) ├─■─────░─┤ Ry(θ[4]) ├
     ├─────────┤ ░ ├──────────┤ │     ░ ├──────────┤
q_1: ┤ Ry(π/4) ├─░─┤ Rz(θ[1]) ├─■──■──░─┤ Rx(θ[5]) ├
     ├─────────┤ ░ ├──────────┤    │  ░ ├──────────┤
q_2: ┤ Ry(π/4) ├─░─┤ Rx(θ[2]) ├─■──■──░─┤ Rx(θ[6]) ├
     ├─────────┤ ░ ├──────────┤ │     ░ ├──────────┤
q_3: ┤ Ry(π/4) ├─░─┤ Rx(θ[3]) ├─■─────░─┤ Ry(θ[7]) ├
     └─────────┘ ░ └──────────┘       ░ └──────────┘
Transpileed with Montreal backend, depth = 22
          ┌────────┐┌────┐┌──────────┐┌────┐ ░ ┌─────────┐    ┌────┐  ┌──────────────┐┌──────────┐            ┌───┐┌─────────┐   ┌────┐  ┌─────────┐     »
 q_3 -> 8 ┤ Rz(-π) ├┤ √X ├┤ Rz(3π/4) ├┤ √X ├─░─┤ Rz(π/2) ├────┤ √X ├──┤ Rz(θ[3] + π) ├┤ Rz(-π/2) ├────────────┤ X ├┤ Rz(π/2) ├───┤ √X ├──┤ Rz(π/2) ├─────»
          ├────────┤├────┤├──────────┤├────┤ ░ ├─────────┤    ├────┤  ├──────────────┤└──┬────┬──┘ ┌────────┐ └─┬─┘└──┬────┬─┘┌──┴────┴─┐└─────

## Excitation Preserving circuit

The ``ExcitationPreserving`` circuit preserves the ratio of $|00\rangle$, $|01\rangle +|10\rangle $ and $|11\rangle $ states. To this end, this circuit uses two-qubit interactions of the form
$$  \begin{pmatrix}
    1 & 0 & 0 & 0 \\
    0 & \cos\left(\theta/2\right) & -i\sin\left(\theta/2\right) & 0 \\
    0 & -i\sin\left(\theta/2\right) & \cos\left(\theta/2\right) & 0 \\
    0 & 0 & 0 & e^{-i\phi} 
    \end{pmatrix} $$
for the mode ``'fsim'`` or with $e^{-i\phi} = 1$ for the mode ``'iswap'``.



In [6]:
from qiskit.circuit.library import ExcitationPreserving

n_qubits = 4
ansatz_EP = ExcitationPreserving(n_qubits, 
                              reps=1, 
                              mode='fsim', 
                              entanglement=ent_pairs, 
                              insert_barriers=True,
                              flatten=True
                             )


print("Excitation Preserving ansatz")
print(ansatz_EP.draw(fold=400, idle_wires=False))

c_montreal = transpile(ansatz_EP, backend=fakemontreal, optimization_level=3)
print("Transpileed with Montreal backend, depth = {}".format(c_montreal.depth()))
print(c_montreal.draw(fold=160, idle_wires=False))

c_huayi = transpile(ansatz_EP, backend=fakehuayi, optimization_level=3)
print("Transpileed with Huayi backend, depth = {}".format(c_huayi.depth()))
print(c_huayi.draw(fold=160, idle_wires=False))

Excitation Preserving ansatz
     ┌──────────┐ ░ ┌────────────┐┌────────────┐                                                 ░ ┌───────────┐
q_0: ┤ Rz(θ[0]) ├─░─┤0           ├┤0           ├─■───────────────────────────────────────────────░─┤ Rz(θ[10]) ├
     ├──────────┤ ░ │  Rxx(θ[4]) ││  Ryy(θ[4]) │ │P(θ[5]) ┌────────────┐┌────────────┐           ░ ├───────────┤
q_1: ┤ Rz(θ[1]) ├─░─┤1           ├┤1           ├─■────────┤0           ├┤0           ├─■─────────░─┤ Rz(θ[11]) ├
     ├──────────┤ ░ ├────────────┤├────────────┤          │  Rxx(θ[8]) ││  Ryy(θ[8]) │ │P(θ[9])  ░ ├───────────┤
q_2: ┤ Rz(θ[2]) ├─░─┤0           ├┤0           ├─■────────┤1           ├┤1           ├─■─────────░─┤ Rz(θ[12]) ├
     ├──────────┤ ░ │  Rxx(θ[6]) ││  Ryy(θ[6]) │ │P(θ[7]) └────────────┘└────────────┘           ░ ├───────────┤
q_3: ┤ Rz(θ[3]) ├─░─┤1           ├┤1           ├─■───────────────────────────────────────────────░─┤ Rz(θ[13]) ├
     └──────────┘ ░ └────────────┘└────────────┘                   

## UCC(SD) ansatz (qiskit_nature.second_q.circuit.library)

The UCC(SD) ansatz builder requires the molecle information

In [14]:
from qiskit_nature.units import DistanceUnit
from qiskit_nature.second_q.drivers import PySCFDriver, Psi4Driver
from qiskit_nature.second_q.mappers import JordanWignerMapper,ParityMapper,BravyiKitaevMapper,QubitMapper

# PySCF requires 
with open(".pyscf_conf.py", "w") as f:
    f.write("B3LYP_WITH_VWN5 = True")

mol_geometry = """
O 0.0 0.0 0.0
H 0.45 -0.1525 -0.8454
"""

qmolecule = PySCFDriver(
    atom=mol_geometry.strip(),
    basis='sto3g',
    charge=1,
    spin=0,
    unit=DistanceUnit.ANGSTROM
    ).run()

from qiskit_nature.second_q.circuit.library import UCCSD, HartreeFock
from qiskit_aer.backends.aer_simulator import AerSimulator

uccsd_ansatz = UCCSD(
    qmolecule.num_spatial_orbitals,
    qmolecule.num_particles,
    JordanWignerMapper(),
    initial_state=HartreeFock(
        qmolecule.num_spatial_orbitals,
        qmolecule.num_particles,
        JordanWignerMapper(),
    ),
)

uccsd_lv0 = transpile(uccsd_ansatz, AerSimulator(), optimization_level=0)
uccsd_lv1 = transpile(uccsd_ansatz, AerSimulator(), optimization_level=1)
uccsd_lv2 = transpile(uccsd_ansatz, AerSimulator(), optimization_level=2)
uccsd_lv3 = transpile(uccsd_ansatz, AerSimulator(), optimization_level=3)
print("=== Circuit Depth ===")
print("Level 0 : {}".format( uccsd_lv0.depth() ))
print("Level 1 : {}".format( uccsd_lv1.depth() ))
print("Level 2 : {}".format( uccsd_lv2.depth() ))
print("Level 3 : {}".format( uccsd_lv3.depth() ))
print("=== Level 3 Circuit ===")
uccsd_lv3.draw(fold=120)

=== Circuit Depth ===
Level 0 : 10388
Level 1 : 10388
Level 2 : 8380
Level 3 : 8380
=== Level 3 Circuit ===


global phase: 3π/2
      ┌─────────────┐               ┌───┐┌──────────────┐┌───┐┌──────────────┐                                         »
 q_0: ┤ U2(-π,-π/2) ├───────────────┤ X ├┤ Rz(1.0*t[0]) ├┤ X ├┤ U2(-π/2,π/2) ├─────────────────────────────────────────»
      └┬────────────┤          ┌───┐└─┬─┘└──────────────┘└─┬─┘└────┬───┬─────┘                                    ┌───┐»
 q_1: ─┤ U3(π,-π,0) ├──────────┤ X ├──■────────────────────■───────┤ X ├──────────────────────────────────────────┤ X ├»
       ├────────────┤     ┌───┐└─┬─┘                               └─┬─┘      ┌───┐                          ┌───┐└─┬─┘»
 q_2: ─┤ U3(π,-π,0) ├─────┤ X ├──■───────────────────────────────────■────────┤ X ├──────────────────────────┤ X ├──■──»
       ├────────────┤┌───┐└─┬─┘                                               └─┬─┘┌───┐                ┌───┐└─┬─┘     »
 q_3: ─┤ U3(π,-π,0) ├┤ X ├──■───────────────────────────────────────────────────■──┤ X ├────────────────┤ X ├──■───────»
       └┬──────────┬┘└─┬─┘                                                         └─┬─┘┌──────────────┐└─┬─┘          »
 q_4: ──┤ U2(0,-π) ├───■─────────────────────────────────────────────────────────────■──┤ U2(π/2,-π/2) ├──■────────────»
        ├──────────┤                                                                    └──────────────┘               »
 q_5: ──┤ U2(0,-π) ├───────────────────────────────────────────────────────────────────────────────────────────────────»
      ┌─┴──────────┴┐               ┌───┐┌──────────────┐┌───┐┌──────────────┐                                         »
 q_6: ┤ U2(-π,-π/2) ├───────────────┤ X ├┤ Rz(1.0*t[8]) ├┤ X ├┤ U2(-π/2,π/2) ├─────────────────────────────────────────»
      └┬────────────┤          ┌───┐└─┬─┘└──────────────┘└─┬─┘└────┬───┬─────┘                                    ┌───┐»
 q_7: ─┤ U3(π,-π,0) ├──────────┤ X ├──■────────────────────■───────┤ X ├──────────────────────────────────────────┤ X ├»
       ├────────────┤     ┌───┐└─┬─┘                               └─┬─┘      ┌───┐                          ┌───┐└─┬─┘»
 q_8: ─┤ U3(π,-π,0) ├─────┤ X ├──■───────────────────────────────────■────────┤ X ├──────────────────────────┤ X ├──■──»
       ├────────────┤┌───┐└─┬─┘                                               └─┬─┘┌───┐                ┌───┐└─┬─┘     »
 q_9: ─┤ U3(π,-π,0) ├┤ X ├──■───────────────────────────────────────────────────■──┤ X ├────────────────┤ X ├──■───────»
       └┬──────────┬┘└─┬─┘                                                         └─┬─┘┌──────────────┐└─┬─┘          »
q_10: ──┤ U2(0,-π) ├───■─────────────────────────────────────────────────────────────■──┤ U2(π/2,-π/2) ├──■────────────»
        ├──────────┤                                                                    └──────────────┘               »
q_11: ──┤ U2(0,-π) ├───────────────────────────────────────────────────────────────────────────────────────────────────»
        └──────────┘                                                                                                   »
«      ┌───┐┌───────────────┐┌───┐┌──────────────┐                                            ┌───┐┌──────────────┐»
« q_0: ┤ X ├┤ Rz(-1.0*t[0]) ├┤ X ├┤ U2(π/2,-π/2) ├────────────────────────────────────────────┤ X ├┤ Rz(1.0*t[1]) ├»
«      └─┬─┘└───────────────┘└─┬─┘└────┬───┬─────┘                                       ┌───┐└─┬─┘└──────────────┘»
« q_1: ──■─────────────────────■───────┤ X ├─────────────────────────────────────────────┤ X ├──■──────────────────»
«                                      └─┬─┘      ┌───┐                             ┌───┐└─┬─┘                     »
« q_2: ──────────────────────────────────■────────┤ X ├─────────────────────────────┤ X ├──■───────────────────────»
«                                                 └─┬─┘┌───┐                   ┌───┐└─┬─┘                          »
« q_3: ─────────────────────────────────────────────■──┤ X ├───────────────────┤ X ├──■────────────────────────────»
«                   

### BQSKit compiler

BQSKit can efficiently simplify a deep circuit, but the parameters must be assigned.

It takes a few minutes to compile a circuit of depth ~ 10000.

In [15]:
from bqskit import compile, Circuit
from random import random
from numpy import pi
import os

def bqs_compile(circ, params):
    
    circ_paramed = circ.assign_parameters(params)
    
    bqs_temp = 'uccsd_bqs_temp.qasm'
    with open(bqs_temp, 'w') as file:
        file.write(circ_paramed.qasm())
    
    bqskit_rep_circ = Circuit.from_file(bqs_temp)
    bqskit_comp_circ = compile(bqskit_rep_circ, optimization_level=3)
    circ_bqs = QuantumCircuit.from_qasm_str(bqskit_comp_circ.to('qasm'))

    os.remove(bqs_temp)

    return circ_bqs

params = [0.0] * uccsd_lv3.num_parameters
# params = [2*pi*random() for i in range(uccsd_lv3.num_parameters)]

circ_bqs = bqs_compile(uccsd_lv3, params)

circ_bqs_ionq = transpile(circ_bqs, fakeionq, optimization_level=3)
# circ_bqs_huayi = transpile(circ_bqs, fakehuayi, optimization_level=3) # skipped because num_qubits of ansatz > num_qubits in Huayi
circ_bqs_montreal = transpile(circ_bqs, fakemontreal, optimization_level=3)

print("=== BQSKit simplified circuit ===")
print(circ_bqs.draw(fold=140))

print("=== BQSKit simplified circuit with IonQ backend ===")
print(circ_bqs_ionq.draw(fold=140, idle_wires=False))
# print("=== BQSKit simplified circuit with Huayi backend ===")
# print(circ_bqs_huayi.draw(fold=140, idle_wires=False))
print("=== BQSKit simplified circuit with Monrteal backend ===")
print(circ_bqs_montreal.draw(fold=140, idle_wires=False))

=== BQSKit simplified circuit ===
        ┌──────────────────────────┐                        
 q_0: ──┤ U3(3.1416,7.1623,4.0207) ├────────────────────────
        ├─────────────────────────┬┘                        
 q_1: ──┤ U3(3.1416,6.2976,3.156) ├─────────────────────────
        ├─────────────────────────┴┐                        
 q_2: ──┤ U3(3.1416,0.47639,3.618) ├────────────────────────
       ┌┴──────────────────────────┤                        
 q_3: ─┤ U3(3.1416,-1.6437,1.4979) ├────────────────────────
       └───────────────────────────┘                        
 q_4: ──────────────────────────────────────────────────────
          ┌─────────────────────┐    ┌─────────────────────┐
 q_5: ────┤ U3(π,5.1253,1.9837) ├────┤ U3(π,7.3838,4.2422) ├
         ┌┴─────────────────────┴┐   └─────────────────────┘
 q_6: ───┤ U3(π,-2.3681,0.77352) ├──────────────────────────
        ┌┴───────────────────────┴─┐                        
 q_7: ──┤ U3(3.1416,2.8222,5.9636) ├───────────────

In [52]:
from qiskit.quantum_info import SparsePauliOp
from qiskit.primitives import Estimator
import random

observables = SparsePauliOp(
    [''.join([random.choice('IXYZ') for i in range(12)]) for k in range(20)],
    coeffs=[random.random() for k in range(20)]
)

print(observables)

job1 = Estimator().run(circuits=uccsd_lv3, observables=observables, parameter_values=params)
job2 = Estimator().run(circuits=circ_bqs, observables=observables)

print( job1.result() )
print( job2.result() )

SparsePauliOp(['YYXIXXZZXYIX', 'IIYXXYIZXXYY', 'IIYXYYXYYZII', 'YIZZIXIZXIXZ', 'ZYIXIZIZZIXZ', 'ZIYIYYYIXXYY', 'ZYZXXZYYXIIY', 'ZIZIIYZYYXYX', 'IIIZIXZZYIZY', 'YYIZYZYIXZYX', 'IXXIXZZIYIXX', 'IYXXXIZIIIYZ', 'IIYYYXZZIIII', 'XYZXYYXYYIXZ', 'XZYIIZXYZXII', 'ZXIZXIXZYZXX', 'XYZIXZXYIZZZ', 'YIYIXZZYYYYY', 'ZYIZIYYYIXIZ', 'YIZIXXZYZXYY'],
              coeffs=[0.20331165+0.j, 0.64398627+0.j, 0.13598239+0.j, 0.84581294+0.j,
 0.26039285+0.j, 0.61689255+0.j, 0.70200037+0.j, 0.17679048+0.j,
 0.21465733+0.j, 0.38463631+0.j, 0.81171687+0.j, 0.37941031+0.j,
 0.75518232+0.j, 0.8162221 +0.j, 0.13369175+0.j, 0.58725107+0.j,
 0.08591595+0.j, 0.77581118+0.j, 0.98772282+0.j, 0.38738835+0.j])
EstimatorResult(values=array([-5.47923405e-17]), metadata=[{}])
EstimatorResult(values=array([-3.41521799e-25]), metadata=[{}])


It seems that UCCSD and UCCSD+BQSKit are different.